In [2]:
import math
import numpy as np
import pandas as pd
import scipy
import matplotlib.pyplot as plt
import seaborn as sns
import lightgbm as lgb

from pathlib import Path
from sklearn import model_selection, metrics
from lightgbm import LGBMClassifier, LGBMRegressor

In [29]:
df_train = pd.read_csv("/kaggle/input/playground-series-s4e4/train.csv")
df_test = pd.read_csv("/kaggle/input/playground-series-s4e4/test.csv")
df_original = pd.read_csv("/kaggle/input/abalone-dataset/abalone.csv")
print(f"{df_train.shape=}")
print(f"{df_test.shape=}")

df_train.shape=(90615, 10)
df_test.shape=(60411, 9)


In [31]:
df_original

Sex  Length  Diameter  Height  Whole weight  Shucked weight  \
0      M   0.455     0.365   0.095        0.5140          0.2245   
1      M   0.350     0.265   0.090        0.2255          0.0995   
2      F   0.530     0.420   0.135        0.6770          0.2565   
3      M   0.440     0.365   0.125        0.5160          0.2155   
4      I   0.330     0.255   0.080        0.2050          0.0895   
...   ..     ...       ...     ...           ...             ...   
4172   F   0.565     0.450   0.165        0.8870          0.3700   
4173   M   0.590     0.440   0.135        0.9660          0.4390   
4174   M   0.600     0.475   0.205        1.1760          0.5255   
4175   F   0.625     0.485   0.150        1.0945          0.5310   
4176   M   0.710     0.555   0.195        1.9485          0.9455   

      Viscera weight  Shell weight  Rings  
0             0.1010        0.1500     15  
1             0.0485        0.0700      7  
2             0.1415        0.2100      9  
3             0.1140        0.1550     10  
4             0.0395        0.0550      7  
...              ...           ...    ...  
4172          0.2390        0.2490     11  
4173          0.2145        0.2605     10  
4174          0.2875        0.3080      9  
4175          0.2610        0.2960     10  
4176          0.3765        0.4950     12  

[4177 rows x 9 columns]

In [32]:
df_train["Sex"] = df_train['Sex'].astype("category")
df_test["Sex"] = df_test['Sex'].astype("category")
df_original["Sex"] = df_original['Sex'].astype("category")
df_original.columns= df_train.drop('id',axis=1).columns

In [4]:
!pip install ydata-profiling

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 59.0 MB/s eta 0:00:00:00:0100:01
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.4
    Uninstalling numpy-1.26.4:
      Successfully uninstalled numpy-1.26.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
keras-nlp 0.9.3 requires keras-core, which is not installed.
tensorflow-decision-forests 1.8.1 requires wurlitzer, which is not installed.
apache-beam 2.46.0 requires dill<0.3.2,>=0.3.1.1, but you have dill 0.3.8 which is incompatible.
apache-beam 2.46.0 requires numpy<1.25.0,>=1.14.3, but you have numpy 1.25.2 which is incompatible.
apache-beam 2.46.0 requires pyarrow<10.0.0,>=3.0.0, but you have pyarrow 15.0.2 which is incompatible.
libpysal 4.9.2 requires packaging>=22, but you have packaging 21.3 which is incompatible.
libpysal 4.9.2 requires shapely>=2.0.1, but you have sh

In [8]:
df = df_train.drop(['Sex','id'],axis=1)

In [9]:
from ydata_profiling import ProfileReport
ProfileReport(df)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Adversial Validation

In [33]:
# Merge train with test/original data use dataset as target label
df_adv_train_test = pd.concat([
    df_train.drop(['id','Rings'],axis=1).assign(dataset='train'),
    df_test.drop(['id'],axis=1).assign(dataset='test')
])

df_adv_train_original = pd.concat([
    df_train.drop(['id'],axis=1).assign(dataset='train'),
    df_original.assign(dataset='original')
])

In [34]:
def auc_score(df_adv_train_test):
    X_train,X_test,y_train,y_test = model_selection.train_test_split(df_adv_train_test.drop(['dataset'],axis=1),
                                                                df_adv_train_test['dataset'],
                                                                test_size=0.33,
                                                                random_state=42)
    clf = LGBMClassifier()
    clf.fit(X_train,y_train)
    pred_proba = clf.predict_proba(X_test)
    auc_score = metrics.roc_auc_score(y_test,pred_proba[:,1])
    print(f"{auc_score=}")


In [35]:
auc_score(df_adv_train_test)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 60710, number of negative: 40477
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.008514 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1342
[LightGBM] [Info] Number of data points in the train set: 101187, number of used features: 8
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.599978 -> initscore=0.405375
[LightGBM] [Info] Start training from score 0.405375
auc_score=0.5014005799476007


In [36]:
auc_score(df_adv_train_original)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 60687, number of negative: 2823
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.016104 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1359
[LightGBM] [Info] Number of data points in the train set: 63510, number of used features: 9
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.955550 -> initscore=3.067929
[LightGBM] [Info] Start training from score 3.067929
auc_score=0.5955402764764435


# Baseline model

In [37]:
ensemble = []
arr_oof_pred = np.zeros(len(df_train))
kf = model_selection.KFold(n_splits=10,shuffle=True,random_state=42)

for fold_no, (train_idx,val_idx) in enumerate(kf.split(df_train)):
    print(f"Starting fold {fold_no}")
    
    df_train_fold = df_train.drop(['id','Rings'],axis=1).iloc[train_idx]
    df_val_fold = df_train.drop(['id','Rings'],axis=1).iloc[val_idx]
    print(f"{df_train_fold.shape=},{df_val_fold.shape=}")
    
    ser_targets_train_fold = df_train['Rings'].iloc[train_idx]
    ser_targets_val_fold = df_train['Rings'].iloc[val_idx]
    
    estimator = LGBMRegressor()
    estimator.fit(df_train_fold,ser_targets_train_fold)
    arr_oof_pred[val_idx] = estimator.predict(df_val_fold)
    estimator.booster_.save_model(f"lgb_regressor_fold_{fold_no}.txt")

Starting fold 0
df_train_fold.shape=(72492, 8),df_val_fold.shape=(18123, 8)
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014783 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1331
[LightGBM] [Info] Number of data points in the train set: 72492, number of used features: 8
[LightGBM] [Info] Start training from score 9.697111
Starting fold 1
df_train_fold.shape=(72492, 8),df_val_fold.shape=(18123, 8)
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.022259 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1331
[LightGBM] [Info] Number of data points in the train set: 72492, number of used features: 8
[LightGBM] [Info] Start training from score 9.704657
Starti

In [39]:
rmsle = metrics.mean_squared_log_error(y_true=df_train['Rings'],y_pred=arr_oof_pred,squared=False)
print(f"{rmsle=}")

rmsle=0.150447207084612


In [40]:
df_train_oof = df_train.copy().assign(arr_oof_prediction=arr_oof_pred)
df_train_oof.to_pickle("df_train_oof.pkl")

In [42]:
folder = Path("/kaggle/working")
estimator_paths = list(folder.glob("lgb_regressor_fold_*"))
display(estimator_paths)

arr_predictions_list: list[np.ndarray] = []

for path in estimator_paths:
    estimator = lgb.Booster(model_file=path)
    arr_predictions_list.append(estimator.predict(df_test.drop(['id'],axis=1)))

arr_mean_predictions = np.mean(arr_predictions_list,axis=0)
print(f"{arr_mean_predictions=}")
arr_mean_predictions

[PosixPath('/kaggle/working/lgb_regressor_fold_3.txt'),
 PosixPath('/kaggle/working/lgb_regressor_fold_4.txt'),
 PosixPath('/kaggle/working/lgb_regressor_fold_2.txt'),
 PosixPath('/kaggle/working/lgb_regressor_fold_1.txt'),
 PosixPath('/kaggle/working/lgb_regressor_fold_0.txt')]

arr_mean_predictions=array([ 9.71942811,  9.64543601, 10.20661262, ..., 12.1223821 ,
       13.65927758,  8.61816023])


array([ 9.71942811,  9.64543601, 10.20661262, ..., 12.1223821 ,
       13.65927758,  8.61816023])

In [44]:
df_submission = pd.DataFrame({'id':df_test['id'],
                             'Rings': arr_mean_predictions})
df_submission.to_csv("submission.csv",index=False)
df_submission

id      Rings
0       90615   9.719428
1       90616   9.645436
2       90617  10.206613
3       90618  10.317335
4       90619   7.566697
...       ...        ...
60406  151021   6.419985
60407  151022   9.294396
60408  151023  12.122382
60409  151024  13.659278
60410  151025   8.618160

[60411 rows x 2 columns]